In [1]:
import pandas as pd
import numpy as np
import os
import json
import csv

TL_sentence_path = r'C:\Users\edcrf\sentence_dataTL.csv'
VL_sentence_path = r'C:\Users\edcrf\sentence_dataVL.csv'

# data파일 불러오기
TL_sentence_data = pd.read_csv(TL_sentence_path, encoding='utf-8')
VL_sentence_data = pd.read_csv(VL_sentence_path, encoding='utf-8')

# 중복 제거, Pronuncication 열은 필요 없다고 생각
TL_sentence_data.drop('Pronunciation', axis=1, inplace=True)
TL_sentence_data = TL_sentence_data.drop_duplicates().reset_index(drop=True)
VL_sentence_data.drop('Pronunciation', axis=1, inplace=True)
VL_sentence_data = VL_sentence_data.drop_duplicates().reset_index(drop=True)

In [2]:
all_sentences = TL_sentence_data.append(VL_sentence_data, ignore_index=True)
print(len(TL_sentence_data), len(VL_sentence_data), len(all_sentences))

323371 44584 367955


In [3]:
from tqdm import tqdm

# 형태소 분석기로 Okt를 사용
import konlpy
from konlpy.tag import Kkma, Komoran, Okt, Hannanum
okt = Okt()

standard_sentences = all_sentences['Standard']
dialect_sentences = all_sentences['Dialect']

In [4]:
data = {
    "src": dialect_sentences, 
    "tar": standard_sentences
}

In [ ]:
# print(data[5])

In [7]:
type(data)

dict

In [8]:
data_df = pd.DataFrame(data)
data_df[:5]

src  \
0  여기는 옥수갱이 잘 된다 카던디 옥수갱이 말고는 무신 농사를 많이 짓습니껴   
1       장례 관련해서 초상집 같은 데 가가 하지 말아야 데는 기 있습니껴   
2       예전에는 집 안에서 여자들이 남자 위로 띠넘으면 안 덴다 캤습니껴   
3    음식을 많이 장만하려고 하면 일손이 모자라서 음식하기가 안 힘들었습니까   
4  이 구두 하나만 계속 신고 댕기이꺼네 인자 굽이 많이 닳아서 갈아야 되겠네   

                                        tar  
0   여기는 옥수수 잘 된다 하던데 옥수수 말고는 무슨 농사를 많이 짓습니까  
1      장례 관련해서 초상집 같은 데 가서 하지 말아야 데는 게 있습니까  
2     예전에는 집 안에서 여자들이 남자 위로 뛰어넘으면 안 된다 했습니까  
3   음식을 많이 장만하려고 하면 일손이 모자라서 음식하기가 안 힘들었습니까  
4  이 구두 하나만 계속 신고 다니니까 이제 굽이 많이 닳아서 갈아야 되겠네

In [9]:
# 데이터 중에서 겹치는 표준어 문장과 방언 문장 제거
filtered_data = {
    "src": [],
    "tar": []
}

for i in range(0, len(standard_sentences)):
    if (standard_sentences[i] != dialect_sentences[i]):
        filtered_data["src"].append(dialect_sentences[i])
        filtered_data["tar"].append(standard_sentences[i])

filtered_df = pd.DataFrame(filtered_data)

filtered_df[:5]

src  \
0  여기는 옥수갱이 잘 된다 카던디 옥수갱이 말고는 무신 농사를 많이 짓습니껴   
1       장례 관련해서 초상집 같은 데 가가 하지 말아야 데는 기 있습니껴   
2       예전에는 집 안에서 여자들이 남자 위로 띠넘으면 안 덴다 캤습니껴   
3  이 구두 하나만 계속 신고 댕기이꺼네 인자 굽이 많이 닳아서 갈아야 되겠네   
4       콩이파리는 가시가 있어가 꺼끄럽고 뻣뻣하고 묵어 보면 맛이 없어예   

                                        tar  
0   여기는 옥수수 잘 된다 하던데 옥수수 말고는 무슨 농사를 많이 짓습니까  
1      장례 관련해서 초상집 같은 데 가서 하지 말아야 데는 게 있습니까  
2     예전에는 집 안에서 여자들이 남자 위로 뛰어넘으면 안 된다 했습니까  
3  이 구두 하나만 계속 신고 다니니까 이제 굽이 많이 닳아서 갈아야 되겠네  
4        콩잎은 가시가 있어서 껄끄럽고 뻣뻣하고 먹어 보면 맛이 없어요

In [10]:
# 표준어 문장 데이터 앞 뒤애 시작과 끝 토큰 추가
filtered_df['tar'] = '<SOS> ' + filtered_df['tar'] + ' <EOS>'

filtered_df[:5]

src  \
0  여기는 옥수갱이 잘 된다 카던디 옥수갱이 말고는 무신 농사를 많이 짓습니껴   
1       장례 관련해서 초상집 같은 데 가가 하지 말아야 데는 기 있습니껴   
2       예전에는 집 안에서 여자들이 남자 위로 띠넘으면 안 덴다 캤습니껴   
3  이 구두 하나만 계속 신고 댕기이꺼네 인자 굽이 많이 닳아서 갈아야 되겠네   
4       콩이파리는 가시가 있어가 꺼끄럽고 뻣뻣하고 묵어 보면 맛이 없어예   

                                                 tar  
0  <SOS> 여기는 옥수수 잘 된다 하던데 옥수수 말고는 무슨 농사를 많이 짓습니까 ...  
1   <SOS> 장례 관련해서 초상집 같은 데 가서 하지 말아야 데는 게 있습니까 <EOS>  
2  <SOS> 예전에는 집 안에서 여자들이 남자 위로 뛰어넘으면 안 된다 했습니까 <EOS>  
3  <SOS> 이 구두 하나만 계속 신고 다니니까 이제 굽이 많이 닳아서 갈아야 되겠네...  
4     <SOS> 콩잎은 가시가 있어서 껄끄럽고 뻣뻣하고 먹어 보면 맛이 없어요 <EOS>

In [11]:
# 토큰화 함수 정의
def tokenize(sentences):
    tokens = set()  # 중복 제거
    for sentence in sentences:
        tokens.update(sentence.split()) # 띄어쓰기 기준 분리
    return list(tokens)

In [12]:
dialect_tokens = tokenize(filtered_df['src'])
standard_tokens = tokenize(filtered_df['tar'])

In [13]:
dialect_vocab = {word: i for i, word in enumerate(dialect_tokens)}
standard_vocab = {word: i for i, word in enumerate(standard_tokens)}

In [14]:
print("방언 사전:", dialect_vocab)
print("표준어 사전:", standard_vocab)

방언 사전: {'뻔했다': 0, '우르르': 1, '징그러운': 2, '간단간단한': 3, '해나이': 4, '없었기': 5, '싱': 6, '후라이로': 7, '맛있더라꼬': 8, '그자이': 9, '가늘라': 10, '정전카니까': 11, '들어온다': 12, '긴': 13, '지형이': 14, '차집에': 15, '꽃이파리나': 16, '문화센터도': 17, '화분도': 18, '티비는': 19, '흘로까': 20, '않애갖고': 21, '가주가': 22, '거싱이': 23, '숨게': 24, '있으니깨네': 25, '사십멫': 26, '음식들이어서': 27, '그랜니더': 28, '괜찮죠': 29, '으니까네': 30, '추우까': 31, '어려법습니더': 32, '햇빛인데': 33, '따다': 34, '눌르든지': 35, '그거에': 36, '늙으니께네': 37, '거던': 38, '끈는': 39, '키하고': 40, '인나야지': 41, '거코': 42, '갈라내고': 43, '내리고': 44, '하셨는교': 45, '히말라야': 46, '허잖아요': 47, '온께는': 48, '데겠다꼬': 49, '모하고로': 50, '라파엘': 51, '이야기하자면': 52, '찌마': 53, '연기가': 54, '대명동으로': 55, '이병철이': 56, '개천': 57, '비치서': 58, '동글동글': 59, '들면서부터는': 60, '그랬었는데': 61, '했자나예': 62, '항아리를': 63, '위예는': 64, '하야면': 65, '만있다': 66, '위암을': 67, '채를썰어': 68, '두드리기': 69, '해야된디': 70, '치왔지': 71, '뜨거운이': 72, '물들이디딘': 73, '캈다가': 74, '시켰으이께네': 75, '아오이': 76, '으실으실한': 77, '사있기네': 78, '손이니까': 79, '벌리고': 80, '배수구에': 81, '돌아보니께': 82, '댕기가다': 83, '나샀다': 84, '저나도': 85, '

In [17]:
# 정수화하는 함수 정의
def integerize_sentence(sentence, vocab):
    tokens = sentence.split()
    integerized_sentence = [vocab[token] for token in tokens]
    return integerized_sentence

In [18]:
indices_dialect_sentences = [integerize_sentence(sentence, dialect_vocab) for sentence in filtered_df['src']]
indices_standard_sentences = [integerize_sentence(sentence, standard_vocab) for sentence in filtered_df['tar']]